# USA Company Valuation with ChatGPT - Part 2

## <a class="anchor" id="3-bullet" href="#toc">3. Quantitative Analysis</a>

In this step we are going to collect and process financial data.

Let's see step by step the algorithm for our valuation model (quantitative).

Valuation is done following principles teached by Prof. Damodaran in his Valuation Course.

We build 4 different scenarios for both FCFF and Dividends Valuation:
1. Earnings TTM & Historical Growth
2. Earnings Normalized & Historical Growth
3. Earnings TTM & Growth TTM
4. Earnings Normalized & Growth Normalized

Each scenario is also run with a recession hypothesis.
We compute a median value for FCFF, Recession FCFF, Dividends, Recession Dividends and then compute 2 Expected Values based on the recession_probability.

These 2 values are then used to compute the final valuation (value/share) skewing the result towards the lowest value (to be conservative).

But let's start from the beginning.

First we are gonna download financial data for our company and save them in MongoDB.

In [25]:
cik = '0001652044'

In [26]:
def download_financial_data(cik):
    """
    Download financial data for a company.
    Upsert document on mongodb (each requests returns the entire history)
    :param cik: company cik
    :return:
    """
    url = f"https://data.sec.gov/api/xbrl/companyfacts/CIK{cik}.json"
    response = make_edgar_request(url)
    
    try:
        r = response.json()
        r["_id"] = cik
        r["url"] = url
        mongodb.upsert_document("financial_data", r)
        
    # ETFs, funds, trusts do not have financial information
    except:
        print(f"ERROR {cik} - {response} - {url}")
        print(company_from_cik(cik))
        
print(cik)
download_financial_data(cik)

doc = mongodb.get_document("financial_data", cik)
doc

0001652044


{'_id': '0001652044',
 'cik': 1652044,
 'entityName': 'Alphabet Inc.',
 'facts': {'dei': {'EntityPublicFloat': {'label': 'Entity Public Float',
    'description': "The aggregate market value of the voting and non-voting common equity held by non-affiliates computed by reference to the price at which the common equity was last sold, or the average bid and asked price of such common equity, as of the last business day of the registrant's most recently completed second fiscal quarter.",
    'units': {'USD': [{'end': '2015-06-30',
       'val': 0,
       'accn': '0001652044-16-000012',
       'fy': 2015,
       'fp': 'FY',
       'form': '10-K',
       'filed': '2016-02-11'},
      {'end': '2015-06-30',
       'val': 0,
       'accn': '0001652044-16-000022',
       'fy': 2015,
       'fp': 'FY',
       'form': '8-K',
       'filed': '2016-05-03',
       'frame': 'CY2015Q2I'},
      {'end': '2016-06-30',
       'val': 413800000000,
       'accn': '0001652044-17-000008',
       'fy': 2016,
 

For the following steps we are going to import methods from our quantitative_analysis module.

We will provide a description of what the function does, but we are not going to delve into much detail here because it pretty menial work of parsing and elaborating data, which would distract you from the main high-level goal of valuating the company and estimate its risks.

if you are interested in the details you are welcome to take a look at the code of the project.

In [27]:
from quantitative_analysis import *

### General Information

The goals of this first phase is extracting the financial data and the general information for our company.

Let's extract financial data required for valuation from company financial document. We have 3 different kind of measures in the result dictionary:

- mr_ measures: these are the most recent values in the financial data (they come from the most recent 10-K or 10-Q
- ttm_ measures: these are the Trailing 12 months measures, meaning the value from the 4 most recent quarters. If the most recent filing is a 10-K that value is equal to the ttm value. Otherwise it needs to be calculated.
- yearly measures: Simply the yearly values coming from the 10-Ks

The format for mr and ttm measures is {"date": date, "value": value}

The format for yearly measures is {"dates": [], "values": []}

In [28]:
data = extract_company_financial_information(cik)
data

{'mr_shares': {'date': Timestamp('2023-03-31 00:00:00'), 'value': 12722000000},
 'shares': {'dates': [2014, 2015, 2016, 2017, 2018, 2019, 2020, 2021, 2022],
  'values': [680172000,
   687348000,
   691293000,
   694783000,
   695556000,
   688335000,
   675222000,
   13242000000,
   12849000000]},
 'ttm_revenue': {'date': Timestamp('2022-12-31 00:00:00'),
  'value': 284612000000},
 'ttm_gross_profit': {'date': None, 'value': 0},
 'ttm_ebit': {'date': Timestamp('2022-12-31 00:00:00'), 'value': 72163000000},
 'ttm_net_income': {'date': Timestamp('2022-12-31 00:00:00'),
  'value': 58587000000},
 'ttm_interest_expenses': {'date': Timestamp('2022-12-31 00:00:00'),
  'value': 354000000},
 'revenue': {'dates': [2013,
   2014,
   2015,
   2016,
   2017,
   2018,
   2019,
   2020,
   2021,
   2022],
  'values': [55519000000,
   66001000000,
   74989000000,
   90272000000,
   110855000000,
   136819000000,
   161857000000,
   182527000000,
   257637000000,
   282836000000]},
 'gross_profit': {'d

Then we look for company revenues to check if there is financial data.

We want to consider the last 5 years in the valuation.

In [29]:
# how many financial years to consider in the valuation 
years = 5
final_year = data["revenue"]["dates"][-1]
initial_year = final_year - years + 1
print(f"Initial Year: {initial_year} - Final Year: {final_year}")

Initial Year: 2018 - Final Year: 2022


We are gonna retrieve the Equity Risk Premium from damodaran data, that we saved in our postgreSQL DB.

Equity Risk Premium is the expected return an investor can expect to achieve by investing in the stock market compared to a riskfree government bond investment.

In [30]:
erp = get_df_from_table("damodaran_erp")
erp = erp[erp["date"] == erp["date"].max()]["value"].iloc[0]
print(f"ERP {erp}")

ERP 0.0525


Let's retrieve the company info and real time price per share (via Yahoo Finance API).

In [31]:
company_info = company_from_cik(cik)
print(company_info)
ticker = company_info["ticker"]
price_per_share = get_current_price_from_yahoo(ticker)
print(f"Price per share {price_per_share}")

cik            0001652044
name        Alphabet Inc.
ticker              GOOGL
exchange           Nasdaq
Name: 2, dtype: object
Price per share 120.81


Let's retrieve some additional info using the company ticker from data we have stored in PostgreSQL (which we collected from Yahoo Finance). 

In [32]:
company_name, country, industry, region = get_generic_info(ticker)
print(f"Company Name: {company_name}")
print(f"Country: {country}")
print(f"Industry: {industry}")
print(f"Region: {region}")

yahoo_equity_ticker = get_df_from_table("yahoo_equity_tickers", f"where symbol = '{ticker}'", most_recent=True).iloc[0]
db_curr = yahoo_equity_ticker["currency"]
db_financial_curr = yahoo_equity_ticker["financial_currency"]

Company Name: Alphabet Inc.
Country: United States
Industry: Information Services
Region: US


This is not the case but if db_curr and db_financial_curr are different it means the quote currency (the currency in which shares are priced) and financial currency (the currency in which financial statements are presented) are different.

In this case we need the forex rate to be able to convert between the two.

We also need the forex rate between the financial currency and USD (in case they are different) to be able to compute the market cap in USD (which we use to estimate the company size).

In [33]:
fx_rate = None

# they are different
if db_curr != db_financial_curr:
    fx_rate = convert_currencies(db_curr, db_financial_curr)

fx_rate_financial_USD = 1

if db_financial_curr != "USD":
    fx_rate_financial_USD = convert_currencies("USD", db_financial_curr)

print(f"FX rate: {fx_rate} - {fx_rate_financial_USD}")

FX rate: None - 1


Retrieve bond_spread DataFrame from damodaran data that we uploaded in our postgreSQL DB.

This is used to estimate the company spread based on its interest coverage ratio = EBIT / Interest Expenses

In [34]:
damodaran_bond_spread = get_df_from_table("damodaran_bond_spread", most_recent=True)
damodaran_bond_spread["greater_than"] = pd.to_numeric(damodaran_bond_spread["greater_than"])
damodaran_bond_spread["less_than"] = pd.to_numeric(damodaran_bond_spread["less_than"])
damodaran_bond_spread

greater_than      less_than    rating                spread  created_at
0     -100000.00       0.199999      D2/D                   0.2  2023-06-23
1           0.20       0.649999      C2/C                 0.175  2023-06-23
2           0.65       0.799999    Ca2/CC                0.1578  2023-06-23
3           0.80       1.249999   Caa/CCC                0.1157  2023-06-23
4           1.25       1.499999     B3/B-                0.0737  2023-06-23
5           1.50       1.749999      B2/B                0.0526  2023-06-23
6           1.75       1.999999     B1/B+                0.0455  2023-06-23
7           2.00       2.250000    Ba2/BB                0.0313  2023-06-23
8           2.25       2.499990   Ba1/BB+                0.0242  2023-06-23
9           2.50       2.999999  Baa2/BBB                  0.02  2023-06-23
10          3.00       4.249999     A3/A-  0.016200000000000003  2023-06-23
11          4.25       5.499999      A2/A  0.014199999999999999  2023-06-23
12          5.50       6.499999     A1/A+                0.0123  2023-06-23
13          6.50       8.499999    Aa2/AA                0.0085  2023-06-23
14          8.50  100000.000000   Aaa/AAA                0.0069  2023-06-23

Make sure to retrieve last annual report (10-K on SEC)

In [35]:
doc = get_last_document(cik, "10-K")
doc

{'_id': 'https://www.sec.gov/Archives/edgar/data/1652044/000165204423000016/goog-20221231.htm',
 'html': '<?xml version="1.0" ?><!--XBRL Document Created with Wdesk from Workiva--><!--Copyright 2023 Workiva--><!--r:94db13ab-d0fb-433a-a7d1-96ca74a2a87d,g:b8c6572a-40d9-4f2f-b3df-2328dc788b5b,d:a96e4fb0476549c99dc3a2b2368f643f--><html xmlns:country="http://xbrl.sec.gov/country/2022" xmlns:iso4217="http://www.xbrl.org/2003/iso4217" xmlns="http://www.w3.org/1999/xhtml" xmlns:ixt="http://www.xbrl.org/inlineXBRL/transformation/2020-02-12" xmlns:goog="http://www.google.com/20221231" xmlns:xlink="http://www.w3.org/1999/xlink" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xmlns:dei="http://xbrl.sec.gov/dei/2022" xmlns:ix="http://www.xbrl.org/2013/inlineXBRL" xmlns:srt="http://fasb.org/srt/2022" xmlns:xbrli="http://www.xbrl.org/2003/instance" xmlns:ixt-sec="http://www.sec.gov/inlineXBRL/transformation/2015-08-31" xmlns:us-gaap="http://fasb.org/us-gaap/2022" xmlns:link="http://www.xbrl.org

Extract business segments and compute geographic distributions.

From the most recent 10-K we are going to extract information about where the company is doing business.
We want to consider the business risk not just based on the country in which the company is incorporated, but more importantly based on the countries where it's conducting business.

In [36]:
segments = extract_segments(doc)
geo_segments_df = geography_distribution(segments, ticker)
geo_segments_df

value       country               country_area  region
0  0.479977  UnitedStates               UnitedStates      US
1  0.204515       Germany             Western Europe  Europe
2  0.043825  Saudi Arabia                Middle East   emerg
3  0.043825   SouthAfrica                     Africa   emerg
4  0.167419         China                       Asia   emerg
5  0.060439        Mexico  Central and South America   emerg

Retrieve country statistics from damodaran data in our postgreSQL DB.
 
Here we have average metrics of the companies in the country (like PE, PEG, EV/Sales, ...) but also country specific metrics like Tax Rate, Country Risk Premium, Moody's rating for the country, ...

For this last set of metrics we have also the same metrics for region (North America, Western Europe, Asia, ...)

In [37]:
country_stats = get_df_from_table("damodaran_country_stats", most_recent=True)
country_stats

country                 pe                 peg  \
0           Liechtenstein  15.03076923076923                None   
1               Argentina   11.5045871559633  0.5843443469282394   
2               Australia  19.30132450331126   2.386433103564577   
3                 Austria  20.12588792423047   1.273790374951295   
4              Azerbaijan   7.51293103448276                None   
..                    ...                ...                 ...   
118  EasternEurope&Russia               None                None   
119            MiddleEast               None                None   
120          NorthAmerica               None                None   
121         WesternEurope               None                None   
122                Global               None                None   

                   pbv                  ps          ev_ebitda  \
0    0.744286439817166   3.615542763157895               None   
1     1.26813880126183  0.9422632794457275   9.06578947368421   
2    2.664233576642336   6.227410144440713  13.43498452012384   
3    1.115204495785201   1.293035437144335  10.44125326370757   
4    1.407915993537965   1.707149853085211  3.147747747747748   
..                 ...                 ...                ...   
118               None                None               None   
119               None                None               None   
120               None                None               None   
121               None                None               None   
122               None                None               None   

              ev_sales moody_rating adjusted_default_spread  \
0                 None          Aaa                     0.0   
1    1.167701863354037           Ca     0.14682729357798166   
2    6.753153153153153          Aaa                     0.0   
3    1.606434604078204          Aa1    0.004889449541284403   
4    1.368854064642508          Ba1    0.030630963302752296   
..                 ...          ...                     ...   
118               None         None     0.05523863838321001   
119               None         None    0.017766934990427034   
120               None         None                     0.0   
121               None         None    0.010682352271974054   
122               None         None     0.01448509212061963   

      country_risk_premium  created_at alpha_2_code alpha_3_code currency  \
0                      0.0  2023-06-23           LI          LIE      CHF   
1      0.20711819215360386  2023-06-23           AR          ARG      ARS   
2                      0.0  2023-06-23           AU          AUS      AUD   
3    0.0068971777994344076  2023-06-23           AT          AUT      EUR   
4      0.04320879033175085  2023-06-23           AZ          AZE      AZN   
..                     ...         ...          ...          ...      ...   
118    0.07792098212912112  2023-06-23         None            -     None   
119   0.025062475549707256  2023-06-23         None            -     None   
120                    0.0  2023-06-23         None            -     None   
121   0.015068788892060588  2023-06-23         None            -     None   
122   0.020433027266880382  2023-06-23         None            -     None   

      power             tax_rate  
0      None                0.125  
1    0.6091                 0.35  
2    0.2377                  0.3  
3    0.8924                 0.24  
4    1.0251                  0.2  
..      ...                  ...  
118    None  0.18347474471087855  
119    None    0.151813371674751  
120    None                 0.25  
121    None  0.24828912576026474  
122    None  0.24672384803400088  

[123 rows x 16 columns]

Compute tax rate, country default spread and country risk premium based on the countries where the company is making business in.

In [38]:
tax_rate = 0
country_default_spread = 0
country_risk_premium = 0

if geo_segments_df is None or geo_segments_df.empty:
    try:
        filter_df = country_stats[country_stats["country"] == country.replace(" ", "")].iloc[0]
    except:
        filter_df = country_stats[country_stats["country"] == "Global"].iloc[0]
    tax_rate = float(filter_df["tax_rate"])
    country_default_spread = float(filter_df["adjusted_default_spread"])
    country_risk_premium = float(filter_df["country_risk_premium"])
else:
    for _, row in geo_segments_df.iterrows():
        percent = row["value"]
        search_key = row["country_area"]
        try:
            filter_df = country_stats[country_stats["country"] == search_key.replace(" ", "")].iloc[0]
        except:
            filter_df = country_stats[country_stats["country"] == "Global"].iloc[0]
        t = float(filter_df["tax_rate"])
        cds = float(filter_df["adjusted_default_spread"])
        crp = float(filter_df["country_risk_premium"])

        tax_rate += t * percent
        country_default_spread += cds * percent
        country_risk_premium += crp * percent
        
print(f"Tax rate: {tax_rate}")
print(f"Country default spread: {country_default_spread}")
print(f"Country risk premium: {country_risk_premium}")

Tax rate: 0.24944222192426488
Country default spread: 0.0110584953817104
Country risk premium: 0.015599385615470526


Adding country risk premium to our base ERP, we get the final Equity Risk Premium (this means that to invest in a company that is doing business in a risky country, the investor will expect a higher return).

In [39]:
final_erp = float(erp) + country_risk_premium
print(f"Final ERP: {final_erp}")

Final ERP: 0.06809938561547052


Select alpha_3_code from company country. These are three-letter country codes defined in ISO 3166-1. 

This will be used for computing the riskfree rate.

In [40]:
alpha_3_code = country_stats[country_stats["country"] == country.replace(" ", "")].iloc[0]["alpha_3_code"]
print(f"Alpha 3 code: {alpha_3_code}")

Alpha 3 code: USA


To get the riskfree rate, our first attempt is to get the 10y bond yield for the financial currency.

We obtain it by scraping it from investing.com.

As the 10y bond yield is influenced by the country risk, to get the riskfree rate we need to subtract from it the country default spread, as taken from Damodaran.

In case we cannot find the currency on investing.com (this is the case for particularly exotic currencies):
- we compute the riskfree for USA
- we take the inflation rate for USA and for the company country of incorporation
- riskfree = riskfree USA * inflation of the country / inflation in USA

In [41]:
riskfree = currency_bond_yield(db_financial_curr, alpha_3_code, country_stats)
print(f"Risk Free: {riskfree}")

Risk Free: 0.03944


To recap we collected the following general information.

In [42]:
print("===== GENERAL INFORMATION =====\n")
print("ticker", ticker)
print("cik", cik)
print("company_name", company_name)
print("country", country)
print("region", region)
print("industry", industry)
print("financial currency", db_financial_curr)
print("riskfree", riskfree)
print("erp", erp)
print("\n\n")

===== GENERAL INFORMATION =====

ticker GOOGL
cik 0001652044
company_name Alphabet Inc.
country United States
region US
industry Information Services
financial currency USD
riskfree 0.03944
erp 0.0525





### Last Available and Historical Financial Data

The goal of this phase is extracting financial data from our data dictionary in variables that will make subsequential computations easier.

Now let's retrieve the shares number for the last years.

get_selected_years extracts the measure we want for the years we specify.

If one of the years in the period in not available in our data dictionary it will insert a 0 in the list.

In [43]:
mr_shares = data["mr_shares"]["value"] / 1000
shares = get_selected_years(data, "shares", initial_year, final_year)
print(f"MR shares: {mr_shares}")   
print(f"Shares: {shares}")    

MR shares: 12722000.0
Shares: [695556.0, 688335.0, 675222.0, 13242000.0, 12849000.0]


Now we are gonna retrieve some more financial data from our data dictionary.

In [44]:
ttm_revenue = data["ttm_revenue"]["value"] / 1000
ttm_ebit = data["ttm_ebit"]["value"] / 1000
ttm_net_income = data["ttm_net_income"]["value"] / 1000
ttm_dividends = data["ttm_dividends"]["value"] / 1000
ttm_interest_expense = data["ttm_interest_expenses"]["value"] / 1000
mr_cash = data["mr_cash"]["value"] / 1000
mr_securities = data["mr_securities"]["value"] / 1000
mr_debt = data["mr_debt"]["value"] / 1000
mr_equity = data["mr_equity"]["value"] / 1000
ebit = get_selected_years(data, "ebit", initial_year, final_year)
net_income = get_selected_years(data, "net_income", initial_year, final_year)
dividends = get_selected_years(data, "dividends", initial_year, final_year)
capex = get_selected_years(data, "capex", initial_year, final_year)
depreciation = get_selected_years(data, "depreciation", initial_year, final_year)
equity_bv = get_selected_years(data, "equity", initial_year, final_year)
cash = get_selected_years(data, "cash", initial_year, final_year)
securities = get_selected_years(data, "securities", initial_year, final_year)
debt_bv = get_selected_years(data, "debt", initial_year, final_year)
revenue = get_selected_years(data, "revenue", initial_year-1, final_year)

mr_cash_and_securities = mr_cash + mr_securities
cash_and_securities = [sum(x) for x in zip(cash, securities)]

Let's compute the revenue growth and revenue delta, which we will use later on.

In [45]:
# Compute revenue growth
revenue_growth = []
revenue_delta = []
for i in range(len(revenue) - 1):
    revenue_delta.append(revenue[i + 1] - revenue[i])
    try:
        revenue_growth.append(revenue[i + 1] / revenue[i] - 1)
    except:
        revenue_growth.append(0)

# drop 1st element we don't need
revenue = revenue[1:]
revenue_growth = revenue_growth[1:]
print(f"Revenue: {revenue}")
print(f"Revenue Growth: {revenue_growth}")

Revenue: [136819000.0, 161857000.0, 182527000.0, 257637000.0, 282836000.0]
Revenue Growth: [0.18300089899794614, 0.1277053201282614, 0.41150076427049154, 0.09780815643715779]


To get adjusted values from our valuation we are going to perform 2 different tasks as explained by Prof. Damodaran:
1. Capitalize Research and Development
2. Account for Operating Leases

Let's start by capitalizing R&D.

We need to capitalize R&D because accounting standards treat it as an operating expense, while it really is a capital expense because benefits of R&D are to be reaped in a number of years not in the year where the expense is taking place.

By capitalizing R&D:
- we choose a number of amortization years based on the industry the company is operating in
- we calculate the amount of unamortized R&D (which will be added to our Equity book value)
- we compute the current year R&D amortization
- we adjust EBIT and Net income by adding back the current year R&D expenses and subtracting the current year R&D amortization

This usually will increase our EBIT and Net income values, but also increase our Equity book value, thus reducing the ROE (return on equity) and ROC (return on capital)

In [46]:
try:
    r_and_d_amortization_years = r_and_d_amortization[industry]
except:
    print(f"\n#######\nCould not find industry: {industry} mapping. "
          f"Check r_and_d_amortization dictionary.\n#######\n")
    r_and_d_amortization_years = 5

r_and_d = get_selected_years(data, "rd", final_year - r_and_d_amortization_years, final_year)
while len(r_and_d) < years:
    r_and_d.insert(0, 0)

ebit_r_and_d_adj, tax_benefit, r_and_d_unamortized, r_and_d_amortization_cy = capitalize_rd(r_and_d, r_and_d_amortization_years, tax_rate, years)


Let's compute R&D adjusted values

In [47]:
ttm_ebit_adj = ttm_ebit + ebit_r_and_d_adj[-1]
ebit_adj = [sum(x) for x in zip(ebit, ebit_r_and_d_adj)]
ttm_net_income_adj = ttm_net_income + ebit_r_and_d_adj[-1]
net_income_adj = [sum(x) for x in zip(net_income, ebit_r_and_d_adj)]
mr_equity_adj = mr_equity + r_and_d_unamortized[-1]
equity_bv_adj = [sum(x) for x in zip(equity_bv, r_and_d_unamortized)]
capex_adj = [sum(x) for x in zip(capex, r_and_d[-years:])]
depreciation_adj = [sum(x) for x in zip(depreciation, r_and_d_amortization_cy)]
ebit_after_tax = [sum(x) for x in zip([x * (1 - tax_rate) for x in ebit_adj], tax_benefit)]
ttm_eps_adj = ttm_net_income_adj / mr_shares

And now the second step, accounting for operating leases.

We need to account for operating leases because accounting standards treat it as an operating expense (like rent), while it really is debt!

This is because operating leases are a long-term commitment and require a minimum payment for many subsequent years. It's not like a rent where the company can cancel if they desire so. It's more like a long-term loan.

By accounting for Operating leases:
- we add following years commitment to debt (discounting them by the cost of debt as the payments will happen in the future)
- we adjust EBIT based on current year payment compared to a equal amortization payment
- we add the interest part of the current year payment to interest expenses
- we recalculate interest coverage ratio and cost of debt based on these new values

This usually will increase our Debt book value, thus reducing the ROC (return on capital), and potentially increasing the company default spread and the cost of debt.

In [48]:
leases = [
    data["mr_op_leases_expense"]["value"] / 1000,
    data["mr_op_leases_next_year"]["value"] / 1000,
    data["mr_op_leases_next_2year"]["value"] / 1000,
    data["mr_op_leases_next_3year"]["value"] / 1000,
    data["mr_op_leases_next_4year"]["value"] / 1000,
    data["mr_op_leases_next_5year"]["value"] / 1000,
    data["mr_op_leases_after_5year"]["value"] / 1000,
]
last_year_leases = max([i for i, x in enumerate(leases) if x != 0], default=-1)
if last_year_leases != -1:
    ebit_op_adj, int_exp_op_adj, debt_adj, tax_benefit_op, company_default_spread = \
        debtize_op_leases(ttm_interest_expense, ttm_ebit_adj, damodaran_bond_spread, riskfree, country_default_spread,
                      leases, last_year_leases, tax_rate, revenue_growth)
    ttm_ebit_adj += ebit_op_adj[-1]
    ttm_interest_expense_adj = ttm_interest_expense + int_exp_op_adj
    mr_debt_adj = mr_debt + debt_adj[-1]
    ebit_adj = [sum(x) for x in zip(ebit_adj, ebit_op_adj)]
    debt_bv_adj = [sum(x) for x in zip(debt_bv, debt_adj)]
    ebit_after_tax = [sum(x) for x in zip(ebit_after_tax, tax_benefit_op)]

    ttm_ebit_after_tax = ttm_ebit_adj * (1 - tax_rate) + tax_benefit[-1] + tax_benefit_op[-1]
# no leases
else:
    ttm_interest_expense_adj = ttm_interest_expense
    mr_debt_adj = mr_debt
    debt_bv_adj = debt_bv
    company_default_spread = get_spread_from_dscr(12.5, damodaran_bond_spread)
    ttm_ebit_after_tax = ttm_ebit_adj * (1 - tax_rate) + tax_benefit[-1]

Let's compute cost of debt.

In [49]:
cost_of_debt = riskfree + country_default_spread + company_default_spread
print(f"Cost of debt: {cost_of_debt}")

Cost of debt: 0.05739849538171041


Let's compute cash and securities.

These are the most liquid assets the company owns, and we are going to consider them both as Cash (usually this is referred to as Cash and Cash equivalents).

In [50]:
mr_cash_and_securities = mr_cash + mr_securities
cash_and_securities = [sum(x) for x in zip(cash, securities)]
print(f"MR Cash and securities {mr_cash_and_securities}")
print(f"Cash and securities {cash_and_securities}")

MR Cash and securities 110880000.0
Cash and securities [107918000.0, 116379000.0, 131265000.0, 133301000.0, 109410000.0]


We compute both earnings per share and dividends per share using the most recent number of shares (to account for splits, dilution, and buybacks).

In [51]:
eps = [x / mr_shares for x in net_income]
eps_adj = [x/mr_shares for x in net_income_adj]
dividends = [x/mr_shares for x in dividends]
print(f"EPS {eps}")
print(f"EPS Adjusted {eps_adj}")
print(f"Dividends {dividends}")

EPS [2.415972331394435, 2.69949693444427, 3.1653041974532306, 5.976497406068228, 4.7140386731645965]
EPS Adjusted [2.991487715555697, 3.275012318605532, 3.775216015712839, 6.6746454787447504, 5.587774458942515]
Dividends [0.0, 0.0, 0.0, 0.0, 0.0]


Now we are going to compute Working Capital as inventory + receivables + other assets - payables - due to affiliates - due to related.

As explained by Damodaran we want to compute WC = non-cash current assets - non-debt current liabilities

In [52]:
wc = {}
for i in ["inventory", "receivables", "other_assets", "account_payable", "due_to_affiliates", "due_to_related_parties"]:
    val = get_selected_years(data, i, initial_year-1, final_year)
    wc[i] = val
    
df = pd.DataFrame(wc)
df["wc"] = df["inventory"] + df["receivables"] + df["other_assets"] - df["account_payable"] \
           - df["due_to_affiliates"] - df["due_to_related_parties"]

# this compute the difference from the previous row
df["delta_wc"] = df["wc"].diff(1)
df = df.dropna()

working_capital = df["wc"].to_list()
delta_wc = df["delta_wc"].to_list()

print(f"Working capital {working_capital}")
print(f"Delta WC {delta_wc}")

Working capital [21803000.0, 25176000.0, 31559000.0, 42457000.0, 45905000.0]
Delta WC [2872000.0, 3373000.0, 6383000.0, 10898000.0, 3448000.0]


Compute reinvestment as CAPEX + delta Working capital - Depreciation

In [53]:
reinvestment = []
for i in range(len(capex)):
    reinvestment.append(capex_adj[i] + delta_wc[i] - depreciation_adj[i])
print(f"Reinvestment {reinvestment}")

Reinvestment [9314706.717299584, 34242706.71729958, 36423298.15189874, 44419839.78059073, 46048666.66666667]


Compute equity market value (which is the company Market Cap)

In [54]:
equity_mkt = mr_shares * price_per_share
if fx_rate is not None:
    equity_mkt /= fx_rate
print(f"Equity market {equity_mkt}")

Equity market 1536944820.0


Compute debt market value.

In [55]:
debt_mkt = ttm_interest_expense_adj * (1 - (1 + cost_of_debt) ** -6) / cost_of_debt + mr_debt_adj / (1 + cost_of_debt) ** 6
print(f"Debt Market {debt_mkt}")

Debt Market 23519939.485163145


Get company/industry data for sales to capital (reinvestment needs), dividends payout, unlevered beta, operating marging and debt to equity.

These values are computed taking into consideration company values and industry values (for sales to capital, operating margin and debt to equity).

PBV, dividends payout and unlevered beta only take into consideration industry values.

These industry values are taken as usual from data provided by Prof. Damodaran (they represents the average values for the companies operating in a specific industry).

In [56]:
target_sales_capital, industry_payout, pbv, unlevered_beta, target_operating_margin, target_debt_equity = \
get_industry_data(industry, region, geo_segments_df, revenue, ebit_adj, revenue_delta, reinvestment,
                  equity_mkt, debt_mkt, equity_bv_adj, debt_bv_adj, mr_equity_adj, mr_debt_adj)

value not found for  Information Services Europe cash_return
searching now in region  US


Retrieve minority interest and compute the market value of Minority interest by multiplying the book value for the PBV (price to book value) derived from the industry data.

In [57]:
mr_original_min_interest = data["mr_minority_interest"]["value"] / 1000
mr_minority_interest = mr_original_min_interest * pbv
print(f"Minority interest {mr_minority_interest}")

Minority interest 0.0


Retrieve tax benefits.

In [58]:
mr_tax_benefits = data["mr_tax_benefits"]["value"] / 1000
mr_sbc = data["mr_sbc"]["value"] / 1000
print(f"MR Tax benefits {mr_tax_benefits}")
print(f"MR SBC {mr_sbc}")

MR Tax benefits 7500000.0
MR SBC 2138000.0


We have now gathered pretty much all the data we are going to need in our valuation model!

But we still need to compute many more measures starting from these, so stay with us.

In [59]:
print("===== Last Available Data =====\n")
print("Outstanding Shares", mr_shares)
print("Price/Share (price currency)", price_per_share)
print("FX Rate:", 1 if fx_rate is None else fx_rate)
print("FX Rate USD:", fx_rate_financial_USD)
print("ttm_revenue", ttm_revenue)
print("ttm_ebit", ttm_ebit, "=>", ttm_ebit_adj)
print("ttm_net_income", ttm_net_income, "=>", ttm_net_income_adj)
print("ttm_dividends", ttm_dividends)
print("ttm_interest_expense", ttm_interest_expense, "=>", ttm_interest_expense_adj)
print("tax_credit", mr_tax_benefits)
print("\n\n")
print("===== Historical Data =====\n")
print("initial_year", initial_year)
print("revenue", revenue)
print("revenue_delta", revenue_delta)
print("ebit", ebit, "=>", ebit_adj)
print("net_income", net_income, "=>", net_income_adj)
print("dividends", dividends)
print("working_capital", working_capital)
print("delta_WC", delta_wc)
print("capex", capex, "=>", capex_adj)
print("depreciation", depreciation, "=>", depreciation_adj)
print("shares_outstanding", shares)
print("equity_bv", equity_bv, "=>", equity_bv_adj)
print("cash&securities", cash_and_securities)
print("debt_bv", debt_bv, "=>", debt_bv_adj)
print("\n\n")
print("===== R&D =====")
print("r_and_d", r_and_d)
print("amortization_years", r_and_d_amortization_years)
print("\n===== Operating Leases =====")
print("leases", leases)
print("\n===== Segments =====\n")
if geo_segments_df is None:
    print("10-K not found. Check annual report on company website.")
else:
    print(geo_segments_df.to_markdown())
print("\n===== Options =====")
print("mr_sbc", mr_sbc)
print("\n\n")

===== Last Available Data =====

Outstanding Shares 12722000.0
Price/Share (price currency) 120.81
FX Rate: 1
FX Rate USD: 1
ttm_revenue 284612000.0
ttm_ebit 72163000.0 => 83584648.3032728
ttm_net_income 58587000.0 => 69702666.66666667
ttm_dividends 0.0
ttm_interest_expense 354000.0 => 501757.63830892835
tax_credit 7500000.0



===== Historical Data =====

initial_year 2018
revenue [136819000.0, 161857000.0, 182527000.0, 257637000.0, 282836000.0]
revenue_delta [25964000.0, 25038000.0, 20670000.0, 75110000.0, 25199000.0]
ebit [27524000.0, 34231000.0, 41224000.0, 78714000.0, 74842000.0] => [34993722.180461325, 41727809.14328552, 49180762.08925044, 87874560.27907851, 86263648.3032728]
net_income [30736000.0, 34343000.0, 40269000.0, 76033000.0, 59972000.0] => [38057706.71729958, 41664706.71729958, 48028298.151898734, 84914839.78059071, 71087666.66666667]
dividends [0.0, 0.0, 0.0, 0.0, 0.0]
working_capital [21803000.0, 25176000.0, 31559000.0, 42457000.0, 45905000.0]
delta_WC [2872000.0, 337

### Computations

The goal of this phase is crunching the financial data we extracted before to compute all the additional derived metrics that we are going to need in our valuation.

Now we can start to calculate the company expected growth.

We estimate growth in 3 different way:
- bottom up growth estimate with TTM values
- bottom up growth estimate with 5 years normalized values
- historical growth trend

Here we compute the first one (bottom up growth estimate with TTM values).

The formula is growth = return on capital * reinvestment rate ((CAPEX + delta WC) / EBIT after tax)

As we are computing growth_TTM, we will use TTM ROC and TTM reinvestment rate.

The same 3 growth estimates are also calculated for growth in EPS (for our dividends valuation), the difference is that growth in eps is computed as return on equity * reinvestment rate (1 - payout ratio)

In [60]:
roc_last, reinvestment_last, growth_last, roe_last, reinvestment_eps_last, growth_eps_last = \
get_growth_ttm(ttm_ebit_after_tax, ttm_net_income_adj, mr_equity_adj, mr_debt_adj, mr_cash_and_securities,
               reinvestment, ttm_dividends, industry_payout)

Compute ROE and ROC to be used in following methods.

ROC = EBIT after tax / (debt + equity - cash)

ROE = Net Income / equity

In [61]:
roe, roc = get_roe_roc(equity_bv_adj, debt_bv_adj, cash_and_securities, ebit_after_tax, net_income_adj)

Now we compute another estimate of growth (historical growth trend), plus other industries values we'll need later on.

Here we use some heuristics on the historical CAGR obtained by the company to compute a conservative historical growth estimate.

In [62]:
cagr, target_levered_beta, target_cost_of_equity, target_cost_of_debt, target_cost_of_capital = \
get_target_info(revenue, ttm_revenue, country_default_spread, tax_rate, final_erp, riskfree,
                unlevered_beta, damodaran_bond_spread, company_default_spread, target_debt_equity)

Let's now compute normalized values for revenue, EBIT, margin and so on, while also computing the last estimate of growth (bottom up with normalized values)

To normalize values we use a weighted average of the values in the 5 years we are considering. More recent years get a higher weight, while older years get a lower weight.

The formulas we use to estimate growth normalized are the same we saw for the TTM one, just using normalized values instead of TTM ones for return on capital, reinvestment rate, return on equity and payout ratio.

In [63]:
revenue_5y, ebit_5y, operating_margin_5y, sales_capital_5y, roc_5y, reinvestment_5y, growth_5y, \
net_income_5y, roe_5y, reinvestment_eps_5y, growth_eps_5y = \
get_normalized_info(revenue, ebit_adj, revenue_delta, reinvestment, target_sales_capital,
                ebit_after_tax, industry_payout, cagr, net_income_adj, roe, dividends, eps_adj, roc)

Compute normalized EPS and payout ratio.

In [64]:
eps_5y, payout_5y = get_dividends_info(eps_adj, dividends)

Here we compute cost of capital based on debt to equity, cost of equity and cost of debt.

In this method we also compute the survival probability which estimates the probability that the firm will still be up and running in 10 years.

This is estimated as 1 - company default spread ^ 10

In [65]:
survival_prob, debt_equity, levered_beta, cost_of_equity, equity_weight, debt_weight, cost_of_capital = \
get_final_info(riskfree, cost_of_debt, equity_mkt, debt_mkt, unlevered_beta,
           tax_rate, final_erp, company_default_spread)

Let's now compute the liquidation value, meaning the value of the firm in case of liquidation.

This is estimated by taking:
- cash, securities and real estate properties at book value
- inventory, account receivables and PP&E at 75% of book value
- equity investments at 50% of book value
- all liabilities at book value

In [66]:
mr_receivables = data["mr_receivables"]["value"] / 1000
mr_inventory = data["mr_inventory"]["value"] / 1000
mr_other_current_assets = data["mr_other_assets"]["value"] / 1000
mr_ppe = data["mr_ppe"]["value"] / 1000
mr_property = data["mr_investment_property"]["value"] / 1000
mr_equity_investments = data["mr_equity_investments"]["value"] / 1000
mr_total_liabilities = data["mr_liabilities"]["value"] / 1000

debug = True
try:
    liquidation_value = calculate_liquidation_value(mr_cash, mr_receivables, mr_inventory, mr_securities,
                                                    mr_other_current_assets, mr_property,
                                                    mr_ppe, mr_equity_investments, mr_total_liabilities, equity_mkt,
                                                    mr_debt, mr_equity, mr_original_min_interest,
                                                    mr_minority_interest, debug=debug)
except:
    print(traceback.format_exc())
    liquidation_value = 0

===== Liquidation Value =====

cash 25924000.0
securities 84956000.0
receivables 36036000.0
inventory 2315000.0
other_current_assets_ms 8532000.0
property 0.0
ppe 117560000.0
equity_investments 1600000.0

total_liabilities 108597000.0
debt_bv 15208000.0
equity_bv 260894000.0
minority_interest 0.0 => 0.0
damodaran_liquidation 126415250.0
net_net_wc_liquidation 49166000.0
liquidation_value 74915750.0





Now we finally have all the data we need to start building our valuation model scenarios.

In [67]:
print("===== Growth =====\n")
print("cagr", round(cagr,4))
print("riskfree", round(riskfree,4))
print("\n\n")
print("===== Model Helper Calculation =====\n")
print("roc_last", round(roc_last,4))
print("reinvestment_last", round(reinvestment_last,4))
print("growth_last", round(growth_last,4))
print("ROC history", roc)
print("roc_5y", round(roc_5y,4))
print("Reinvestment history", reinvestment)
print("reinvestment_5y", round(reinvestment_5y,4))
print("growth_5y", round(growth_5y,4))
print("revenue_5y", revenue_5y)
print("ebit_5y", ebit_5y)
print("roe_last", round(roe_last,4))
print("reinvestment_eps_last", round(reinvestment_eps_last,4))
print("growth_eps_last", round(growth_eps_last,4))
print("sales_capital_5y", round(sales_capital_5y,4))
print("roe_5y", round(roe_5y,4))
print("reinvestment_eps_5y", round(reinvestment_eps_5y,4))
print("growth_eps_5y", round(growth_eps_5y,4))
print("eps_5y", round(eps_5y,4))
print("payout_5y", round(payout_5y,4))
print("industry_payout", round(industry_payout,4))
print("target_sales_capital", round(target_sales_capital,4))
print("\n\n")
print("===== Recap Info =====\n")
print("country_default_spread", round(country_default_spread,4))
print("country_risk_premium", round(country_risk_premium,4))
print("riskfree", round(riskfree,4))
print("final_erp", round(final_erp,4))
print("unlevered_beta", round(unlevered_beta,4))
print("tax_rate", round(tax_rate,4))
print("levered_beta", round(levered_beta,4))
print("cost_of_equity", round(cost_of_equity,4))
print("cost_of_debt", round(cost_of_debt,4))
print("equity_weight", round(equity_weight,4))
print("debt_weight", round(debt_weight,4))
print("cost_of_capital", round(cost_of_capital,4))
print("equity_mkt", round(equity_mkt,2))
print("debt_mkt", round(debt_mkt,2))
print("debt_equity", round(debt_equity,4))
print("equity_bv_adj", round(mr_equity_adj,2))
print("debt_bv_adj", round(mr_debt_adj,2))
print("ebit_adj", round(ttm_ebit_adj,2))
print("company_default_spread", round(company_default_spread,4))
print("survival_prob", round(survival_prob,4))
print("liquidation value", round(liquidation_value, 2))
print("\n\n")
print("===== Other Model inputs =====\n")
print("operating_margin_5y", round(operating_margin_5y,4))
print("target_operating_margin", round(target_operating_margin,4))
print("target_debt_equity", round(target_debt_equity,4))
print("target_levered_beta", round(target_levered_beta,4))
print("target_cost_of_equity", round(target_cost_of_equity,4))
print("target_cost_of_debt", round(target_cost_of_debt,4))
print("target_cost_of_capital", round(target_cost_of_capital,4))
print("\n\n")

===== Growth =====

cagr 0.0979
riskfree 0.0394



===== Model Helper Calculation =====

roc_last 0.2632
reinvestment_last 0.7021
growth_last 0.1848
ROC history [0.22135934300621093, 0.22984520957423168, 0.23582586817601423, 0.33667822475994597, 0.2740669576134261]
roc_5y 0.2807
Reinvestment history [9314706.717299584, 34242706.71729958, 36423298.15189874, 44419839.78059073, 46048666.66666667]
reinvestment_5y 0.7246
growth_5y 0.2034
revenue_5y 250874612.9032258
ebit_5y 77367330.4486783
roe_last 0.2108
reinvestment_eps_last 1.0
growth_eps_last 0.2108
sales_capital_5y 1.009
roe_5y 0.2231
reinvestment_eps_5y 1.0
growth_eps_5y 0.2231
eps_5y 5.4014
payout_5y 0.0
industry_payout 0.9536
target_sales_capital 1.5995



===== Recap Info =====

country_default_spread 0.0111
country_risk_premium 0.0156
riskfree 0.0394
final_erp 0.0681
unlevered_beta 1.3355
tax_rate 0.2494
levered_beta 1.3509
cost_of_equity 0.1314
cost_of_debt 0.0574
equity_weight 0.9849
debt_weight 0.0151
cost_of_capital 0.1301
eq

### Valuation

And now, having everything we need, we can perform our valuations for each of the 8 scenarios we presented at the beginning (recession and no recession):
- Earnings TTM & Historical Growth
- Earnings Normalized & Historical Growth
- Earnings TTM & Growth TTM
- Earnings Normalized & Growth Normalized

**Dividends valuation**:
1. Compute EPS for the next 10 years based on growth estimates
2. Compute payout ratio and Dividends/Share for the next 10 years
3. Compute terminal value as 11-year EPS / (cost of equity - growth)
4. Discount everything to today using the cost of equity

**Free Cash Flow valuation**:
1. Compute revenue for the next 10 years based on growth estimates
2. Compute operating margin, EBIT, taxes, reinvestment and FCFF for the next 10 years
3. Compute terminal value as 11-year FCFF / (cost of capital - growth)
4. Discount everything to today using the cost of capital

Compute liquidation per share

In [68]:
liquidation_per_share = liquidation_value / mr_shares
if fx_rate is not None:
    fcff_value *= fx_rate
    div_value *= fx_rate
    liquidation_per_share *= fx_rate

In [69]:
dict_values_for_bi = {}

stock_value_div_ttm_fixed = dividends_valuation(EARNINGS_TTM, GROWTH_FIXED, cagr, growth_eps_5y, growth_5y,
                                                riskfree, industry_payout, cost_of_equity,
                                                target_cost_of_equity, growth_eps_last, eps_5y, payout_5y, ttm_eps_adj,
                                                reinvestment_eps_last, fx_rate, survival_prob, liquidation_per_share, debug=debug, dict_values_for_bi=dict_values_for_bi)
stock_value_div_norm_fixed = dividends_valuation(EARNINGS_NORM, GROWTH_FIXED, cagr, growth_eps_5y, growth_5y,
                                                 riskfree, industry_payout, cost_of_equity,
                                                 target_cost_of_equity, growth_eps_last, eps_5y, payout_5y, ttm_eps_adj,
                                                reinvestment_eps_last, fx_rate, survival_prob, liquidation_per_share, debug=debug, dict_values_for_bi=dict_values_for_bi)
stock_value_div_ttm_ttm = dividends_valuation(EARNINGS_TTM, GROWTH_TTM, cagr, growth_eps_5y, growth_5y, riskfree,
                                              industry_payout, cost_of_equity, target_cost_of_equity,
                                              growth_eps_last, eps_5y, payout_5y, ttm_eps_adj,
                                                reinvestment_eps_last, fx_rate, survival_prob, liquidation_per_share, debug=debug, dict_values_for_bi=dict_values_for_bi)
stock_value_div_norm_norm = dividends_valuation(EARNINGS_NORM, GROWTH_NORM, cagr, growth_eps_5y, growth_5y, riskfree,
                                                industry_payout, cost_of_equity,
                                                target_cost_of_equity, growth_eps_last, eps_5y, payout_5y, ttm_eps_adj,
                                                reinvestment_eps_last, fx_rate, survival_prob, liquidation_per_share, debug=debug, dict_values_for_bi=dict_values_for_bi)
stock_value_div_ttm_fixed_recession = dividends_valuation(EARNINGS_TTM, GROWTH_FIXED, cagr, growth_eps_5y, growth_5y,
                                                riskfree, industry_payout, cost_of_equity,
                                                target_cost_of_equity, growth_eps_last, eps_5y, payout_5y, ttm_eps_adj,
                                                reinvestment_eps_last, fx_rate, survival_prob, liquidation_per_share, debug=debug, recession=True, dict_values_for_bi=dict_values_for_bi)
stock_value_div_norm_fixed_recession = dividends_valuation(EARNINGS_NORM, GROWTH_FIXED, cagr, growth_eps_5y, growth_5y,
                                                 riskfree, industry_payout, cost_of_equity,
                                                 target_cost_of_equity, growth_eps_last, eps_5y, payout_5y, ttm_eps_adj,
                                                reinvestment_eps_last, fx_rate, survival_prob, liquidation_per_share, debug=debug, recession=True, dict_values_for_bi=dict_values_for_bi)
stock_value_div_ttm_ttm_recession = dividends_valuation(EARNINGS_TTM, GROWTH_TTM, cagr, growth_eps_5y, growth_5y, riskfree,
                                              industry_payout, cost_of_equity, target_cost_of_equity,
                                              growth_eps_last, eps_5y, payout_5y, ttm_eps_adj,
                                                reinvestment_eps_last, fx_rate, survival_prob, liquidation_per_share, debug=debug, recession=True, dict_values_for_bi=dict_values_for_bi)
stock_value_div_norm_norm_recession = dividends_valuation(EARNINGS_NORM, GROWTH_NORM, cagr, growth_eps_5y, growth_5y, riskfree,
                                                industry_payout, cost_of_equity,
                                                target_cost_of_equity, growth_eps_last, eps_5y, payout_5y, ttm_eps_adj,
                                                reinvestment_eps_last, fx_rate, survival_prob, liquidation_per_share, debug=debug, recession=True, dict_values_for_bi=dict_values_for_bi)

stock_value_fcff_ttm_fixed = fcff_valuation(EARNINGS_TTM, GROWTH_FIXED, cagr, riskfree, ttm_revenue, ttm_ebit_adj,
                                            target_operating_margin, mr_tax_benefits, tax_rate, sales_capital_5y, target_sales_capital,
                                            debt_equity, target_debt_equity, unlevered_beta, final_erp, cost_of_debt,
                                            target_cost_of_debt, mr_cash, mr_securities, debt_mkt, mr_minority_interest, survival_prob, mr_shares,
                                            liquidation_value, growth_last, growth_5y, revenue_5y, ebit_5y, fx_rate, mr_property, mr_sbc, debug=debug, dict_values_for_bi=dict_values_for_bi)
stock_value_fcff_norm_fixed = fcff_valuation(EARNINGS_NORM, GROWTH_FIXED, cagr, riskfree, ttm_revenue, ttm_ebit_adj,
                                             target_operating_margin, mr_tax_benefits, tax_rate, sales_capital_5y, target_sales_capital,
                                             debt_equity, target_debt_equity, unlevered_beta, final_erp, cost_of_debt,
                                             target_cost_of_debt, mr_cash, mr_securities, debt_mkt, mr_minority_interest, survival_prob, mr_shares,
                                             liquidation_value, growth_last, growth_5y, revenue_5y, ebit_5y, fx_rate, mr_property, mr_sbc, debug=debug, dict_values_for_bi=dict_values_for_bi)
stock_value_fcff_ttm_ttm = fcff_valuation(EARNINGS_TTM, GROWTH_TTM, cagr, riskfree, ttm_revenue, ttm_ebit_adj,
                                          target_operating_margin, mr_tax_benefits, tax_rate, sales_capital_5y, target_sales_capital,
                                          debt_equity, target_debt_equity, unlevered_beta, final_erp, cost_of_debt,
                                          target_cost_of_debt, mr_cash, mr_securities, debt_mkt, mr_minority_interest, survival_prob, mr_shares,
                                          liquidation_value, growth_last, growth_5y, revenue_5y, ebit_5y, fx_rate, mr_property, mr_sbc, debug=debug, dict_values_for_bi=dict_values_for_bi)
stock_value_fcff_norm_norm = fcff_valuation(EARNINGS_NORM, GROWTH_NORM, cagr, riskfree, ttm_revenue, ttm_ebit_adj,
                                            target_operating_margin, mr_tax_benefits, tax_rate, sales_capital_5y, target_sales_capital,
                                            debt_equity, target_debt_equity, unlevered_beta, final_erp, cost_of_debt,
                                            target_cost_of_debt, mr_cash, mr_securities, debt_mkt, mr_minority_interest, survival_prob, mr_shares,
                                            liquidation_value, growth_last, growth_5y, revenue_5y, ebit_5y, fx_rate, mr_property, mr_sbc, debug=debug, dict_values_for_bi=dict_values_for_bi)
stock_value_fcff_ttm_fixed_recession = fcff_valuation(EARNINGS_TTM, GROWTH_FIXED, cagr, riskfree, ttm_revenue, ttm_ebit_adj,
                                                      target_operating_margin, mr_tax_benefits, tax_rate, sales_capital_5y, target_sales_capital,
                                                      debt_equity, target_debt_equity, unlevered_beta, final_erp, cost_of_debt,
                                                      target_cost_of_debt, mr_cash, mr_securities, debt_mkt, mr_minority_interest, survival_prob, mr_shares,
                                                      liquidation_value, growth_last, growth_5y, revenue_5y, ebit_5y, fx_rate, mr_property, mr_sbc, debug=debug, recession=True, dict_values_for_bi=dict_values_for_bi)
stock_value_fcff_norm_fixed_recession = fcff_valuation(EARNINGS_NORM, GROWTH_FIXED, cagr, riskfree, ttm_revenue, ttm_ebit_adj,
                                                       target_operating_margin, mr_tax_benefits, tax_rate, sales_capital_5y, target_sales_capital,
                                                       debt_equity, target_debt_equity, unlevered_beta, final_erp, cost_of_debt,
                                                       target_cost_of_debt, mr_cash, mr_securities, debt_mkt, mr_minority_interest, survival_prob, mr_shares,
                                                       liquidation_value, growth_last, growth_5y, revenue_5y, ebit_5y, fx_rate, mr_property, mr_sbc, debug=debug, recession=True, dict_values_for_bi=dict_values_for_bi)
stock_value_fcff_ttm_ttm_recession = fcff_valuation(EARNINGS_TTM, GROWTH_TTM, cagr, riskfree, ttm_revenue, ttm_ebit_adj,
                                                    target_operating_margin, mr_tax_benefits, tax_rate, sales_capital_5y, target_sales_capital,
                                                    debt_equity, target_debt_equity, unlevered_beta, final_erp, cost_of_debt,
                                                    target_cost_of_debt, mr_cash, mr_securities, debt_mkt, mr_minority_interest, survival_prob, mr_shares,
                                                    liquidation_value, growth_last, growth_5y, revenue_5y, ebit_5y, fx_rate, mr_property, mr_sbc, debug=debug, recession=True, dict_values_for_bi=dict_values_for_bi)
stock_value_fcff_norm_norm_recession = fcff_valuation(EARNINGS_NORM, GROWTH_NORM, cagr, riskfree, ttm_revenue, ttm_ebit_adj,
                                                      target_operating_margin, mr_tax_benefits, tax_rate, sales_capital_5y, target_sales_capital,
                                                      debt_equity, target_debt_equity, unlevered_beta, final_erp, cost_of_debt,
                                                      target_cost_of_debt, mr_cash, mr_securities, debt_mkt, mr_minority_interest, survival_prob, mr_shares,
                                                      liquidation_value, growth_last, growth_5y, revenue_5y, ebit_5y, fx_rate, mr_property, mr_sbc, debug=debug, recession=True, dict_values_for_bi=dict_values_for_bi)

===== Dividends Valuation - EARNINGS_TTM + GROWTH_FIXED + recession:False =====

expected_growth [0.1074 0.101  0.0946 0.0881 0.0817 0.0753 0.0689 0.0625 0.0561 0.0497
 0.0433]
earnings_per_share [6.0673, 6.6799, 7.3116, 7.9561, 8.6064, 9.2546, 9.8924, 10.5106, 11.1, 11.6513, 12.1552]
payout_ratio [0.0867 0.1734 0.2601 0.3468 0.4335 0.5202 0.6069 0.6935 0.7802 0.8669
 0.9536]
dividends_per_share [0.526, 1.1582, 1.9016, 2.759, 3.7306, 4.8139, 6.0032, 7.2895, 8.6606, 10.1008, 11.5915]
cost_of_equity [0.1315 0.1317 0.1318 0.1319 0.132  0.1321 0.1322 0.1323 0.1324 0.1325
 0.1327]
cumulative_cost_equity [1.1315, 1.2805, 1.4493, 1.6404, 1.8569, 2.1022, 2.3801, 2.6951, 3.052, 3.4565, 3.915]
present_value [0.4648, 0.9045, 1.3121, 1.6819, 2.009, 2.2899, 2.5222, 2.7048, 2.8377, 2.9223]
terminal_value 129.66
PV of terminal_value 33.12
stock value (price curr) 52.77
stock value (fin curr) 49.63



===== Dividends Valuation - EARNINGS_NORM + GROWTH_FIXED + recession:False =====

expected_growth [0.

Now let's compute the Expected values for our valuation.

We take the median value for the 4 FCFF no recession scenarios, and the median value for the 4 FCFF recession scenarios.

We then take the weighted average of these 2 values based on the recession probability.

And of course we do the same for the Dividends scenarios.

In [70]:
fcff_values_list = [stock_value_fcff_ttm_fixed, stock_value_fcff_norm_fixed, stock_value_fcff_ttm_ttm,
                       stock_value_fcff_norm_norm]
fcff_recession_values_list = [stock_value_fcff_ttm_fixed_recession, stock_value_fcff_norm_fixed_recession,
                                          stock_value_fcff_ttm_ttm_recession, stock_value_fcff_norm_norm_recession]
div_values_list = [stock_value_div_ttm_fixed, stock_value_div_norm_fixed, stock_value_div_ttm_ttm,
                   stock_value_div_norm_norm]
div_recession_values_list = [stock_value_div_ttm_fixed_recession, stock_value_div_norm_fixed_recession,
                                         stock_value_div_ttm_ttm_recession, stock_value_div_norm_norm_recession]

recession_probability = 0.5
fcff_value = summary_valuation(fcff_values_list)
fcff_recession_value = summary_valuation(fcff_recession_values_list)
ev_fcff = fcff_value * (1 - recession_probability) + fcff_recession_value * recession_probability
div_value = summary_valuation(div_values_list)
div_recession_value = summary_valuation(div_recession_values_list)
ev_dividends = div_value * (1 - recession_probability) + div_recession_value * recession_probability

The delta variables are the % difference between the value our model assigned to 1 share of the company and the current stock price.

A negative value means the stock is undervalued according to our model.

A positive value means the stock is overvalued according to our model.

In [71]:
fcff_delta = price_per_share / ev_fcff - 1 if fcff_value > 0 else 10
div_delta = price_per_share / ev_dividends - 1 if div_value > 0 else 10
liquidation_delta = price_per_share / liquidation_per_share - 1 if liquidation_per_share > 0 else 10

In [72]:
print("FCFF values")
print([round(x, 2) for x in fcff_values_list])
print("\nFCFF values w/ Recession")
print([round(x, 2) for x in fcff_recession_values_list])
print("\n\nDiv values")
print([round(x, 2) for x in div_values_list])
print("\nDiv values w/ Recession")
print([round(x, 2) for x in div_recession_values_list])

print("\n\n\n")

print("Price per Share", price_per_share)
print("FCFF Result", ev_fcff)
print("FCFF Deviation", fcff_delta)
print("Dividends Result", ev_dividends)
print("Dividends Deviation", div_delta)


FCFF values
[59.31, 54.0, 75.09, 71.83]

FCFF values w/ Recession
[42.92, 39.34, 46.93, 43.88]


Div values
[49.63, 48.93, 79.39, 82.64]

Div values w/ Recession
[35.41, 34.91, 48.82, 49.95]




Price per Share 120.81
FCFF Result 54.485952978997105
FCFF Deviation 1.2172687343207351
Dividends Result 53.31367488976619
Dividends Deviation 1.2660227465053255


### Company Risk Assessment

This last phase is all about estimating risks in investing in the company.

We are going to consider:
- Company size
- Company complexity
- Share dilution in the last 5 years
- Changes in auditor
- Company type
- Consistent growth of inventory and receivables compared to revenue
- Qualitative information we extracted previously using ChatGPT model

In [73]:
market_cap_USD = equity_mkt * fx_rate_financial_USD
if market_cap_USD < 50 * 10 ** 3:
    company_size = "Nano"
elif market_cap_USD < 300 * 10 ** 3:
    company_size = "Micro"
elif market_cap_USD < 2 * 10 ** 6:
    company_size = "Small"
elif market_cap_USD < 10 * 10 ** 6:
    company_size = "Medium"
elif market_cap_USD < 200 * 10 ** 6:
    company_size = "Large"
else:
    company_size = "Mega"
print(f"Company Size {company_size}")

Company Size Mega


For company type we have 7 different possibilities, where a single company can match one or more of them.

The categories are build around the concepts explained by Peter Lynch in his book "One Up on Wall Street".

- fast grower (high growth)
- stalward (moderate growth)
- slow grower (low growth)
- declining (negative growth)
- turn around (money losing company or debt afflicted company with a clear way to turn around)
- asset play (liquidation value higher than market cap)
- cyclical (results affected by business cycle)

In [74]:
complexity = company_complexity(doc, industry, company_size)
dilution = company_share_diluition(shares)
inventory = get_selected_years(data, "inventory", initial_year-1, final_year)
receivables = get_selected_years(data, "receivables", initial_year-1, final_year)
company_type = get_company_type(revenue_growth, mr_debt_adj, equity_mkt, liquidation_value, operating_margin_5y, industry)

In [75]:
auditor = find_auditor(doc)
print(f"Auditor {auditor}")

Auditor Ernst & Young LLP We have served as the Company's auditor since 1999


Here the result of the risk assessment.

In [76]:
print("===== Risk Assessment =====\n")
print("MKT CAP USD: ", market_cap_USD)
print("company_size", company_size)
print("company complexity", complexity)
print("share dilution", round(dilution, 4))
print("revenue", revenue)
print("inventory", inventory)
print("receivables", receivables)
print("company_type", company_type)
print("Auditor", auditor)
print()

===== Risk Assessment =====

MKT CAP USD:  1536944820.0
company_size Mega
company complexity 4
share dilution 1.0732
revenue [136819000.0, 161857000.0, 182527000.0, 257637000.0, 282836000.0]
inventory [749000.0, 1107000.0, 999000.0, 728000.0, 1170000.0, 2670000.0]
receivables [18336000.0, 20838000.0, 25326000.0, 30930000.0, 39304000.0, 40258000.0]
company_type {'fast_grower': True, 'stalward': False, 'slow_grower': False, 'declining': False, 'turn_around': False, 'asset_play': False, 'cyclical': True}
Auditor Ernst & Young LLP We have served as the Company's auditor since 1999



To conclude we can show the qualitative information from the most recent company filings (as shown in the qualitative analysis sections).

This can inform the investor about the company business, the company specific risks, the management view on the future of the company and the industry, and much more.

Having the summary of the most recent 10Qs and 8Ks we can stay up to date with the most recent developments of the company, which is extremely useful when deciding whether to invest.

In [77]:
recent_docs = get_recent_docs(cik, doc["filing_date"])
for d in recent_docs:

    print("##############")
    print(d["form_type"], d["filing_date"], d["_id"])
    print("##############\n")

    if not mongodb.check_document_exists("parsed_documents", d["_id"]):
        parse_document(d)

    parsed_doc = mongodb.get_document("parsed_documents", d["_id"])

    if not mongodb.check_document_exists("items_summary", d["_id"]):
        sections_summary(parsed_doc)

    summary_doc = mongodb.get_document("items_summary", d["_id"])

    for k, v in summary_doc.items():
        if isinstance(v, dict):

            print(f"=== {k} ===")

            for info in v["summary"]:
                print(info)
                
            print()

    print("\n")

##############
10-K 2023-02-03 https://www.sec.gov/Archives/edgar/data/1652044/000165204423000016/goog-20221231.htm
##############

=== business ===
Alphabet Inc., the parent company of Google, is led by CEO Sundar Pichai and focuses on providing access and technology to everyone
Google offers services such as Google Search, YouTube, and Google Assistant, and has a strong presence in the cloud computing industry with Google Cloud
Alphabet's structure allows its businesses to thrive independently
The company is committed to investing in moonshot projects and advancing AI technologies while prioritizing privacy and security for its users and customers
Alphabet also has a portfolio of Other Bets aimed at solving industry problems
They face competition in multiple areas and prioritize developing innovative products and technologies
Sustainability is a core value, with ambitious goals to transition to a carbon-free and circular economy
Alphabet values its culture and workforce, providing a 

## <a class="anchor" id="4-bullet" href="#toc">4. Visualization</a>

We built some dashboards using the 2 main Business Intelligence tools, Tableau and PowerBI.

Using these dashboards we can understand every company we value at a glance using a visual format.

### Tableau Overview

A ticker filter in the top left, let us choose the company we want to visualize. We can see the current price/share and general information at the top.

Then we have a geography segmentation where we can see the distribution of country/region where the company operates.

And finally at the bottom we have two tables were we can explore the summaries of the sections of the most recent filings of the company. (The ones we built before using OpenAI API)

<img src="../images/TB_overview1.PNG">

Clicking the desidered section on the left we can instantly see the summary of that section.

This is pretty awesome, and can save hours and hours of research time.

(We know because we do that for the companies we invest in)

<img src="../images/TB_overview2.PNG">

### PowerBI Overview

We built the same dashboard also in PowerBI, just for fun.

The functionality is pretty much the same.

<img src="../images/PBI_overview1.PNG">

### Tableau Valuation

In this dashboard we can quickly visualize the different valuations we got from our 8 scenarios, both for FCFF valuations and dividends valuations.

Then we have a chart with the estimated revenue, EBIT, FCFF and dividends in the next 10 years.

We can change the scenario we are visualizing by changing the parameters on the right.

At the bottom we can see the components that make up for the company value we estimate, and the estimated value/share.

<img src="../images/TB_valuation1.PNG">

### PowerBI Valuation

We also built this dashboard in PowerBI.

We have some different visual elements here to better leverage the features of the tool, like a waterfall chart instead of a simple bar chart (we could also build that in Tableau, but it would have required a little data crunching to get it to the correct format).

<img src="../images/PBI_valuation2.PNG">

## <a class="anchor" id="5-bullet" href="#toc">5. Conclusions</a>

We have completed this project from data collection to visualization with the goal to build a tool to help up in US company valuation.

### Qualitative analysis results
So far we have seen the **qualitative analysis** in which we extrapolated text from company reports structured it in sections and then summarized the most important ones in key insights to better understand the company and help us valuate the company.

As we can see, for *Alphabet Inc.* we have various insights that can give use a better understanding of what is the company business, what is is mission and how its revenue is structured.

We can further increase our knowledge of what happened in recent periods by reading the quarterly reports (10-Q) and some recent announce major events the company announced (8-K).

### Quantitative analysis results
Then we extrapolated data from financial data of the company, and computed all measures and values to perform the **quantitative analysis**.

In regards to Alphabet Inc. financial data, we can see from the summary of all extrapolated data that is a *fast grower* *Mega* company. 

However, based on the computed valuation scenarios we can see that the company is overpriced at the moment, meaning to avoid a deep analysis of this company.


## Next Steps

The goal of this project is to build a tool to help us better valuate american companies for investing purposes. identifying measures from financial data and extrapolate useful insights from SEC filings.

However, there are various limitaitons that we can identify, that could be further improved for a production ready project, here's a list:
- Manage files larger than 16MB. 
    - Due to mongoDB size limitation we excluded files that are larger than 16MB. This could be solved using a storage system like S3 to save raw files instead that directly on mongoDB.
- better industry segmentation.
    - Understanding the segmentation of company revenue by industry and/or geographic area is not trivial. What we did in this project is a semplification of what can be done. A better segmentation could be done by grouping and average segments as reported by companies.
- better reports section identification.
    - There are some limitation in finding sections inside filings. At the moment we exploit the table of contents or a default items list. This could bring some problems in unidentified cases.
- Improve qualitative analysis including sentiment analysis of the company products.
    - Sentiment analysis is known practice when valuating companies. A possible way to implement could be using twitter APIs or similar to integrate what people say about a company or look on google searches to see trends in company products.
- Industry and industry CAGR to compare with company growth.
    - Retrieve an industry with all its context and its growth could be useful to compare the market with the company growth.
- Aggregate similar risks and define a peer voting system to define risk impact for a specific kind of risk.
    - A possible way to manage subjectivity of assessing risks of a company could be a peer voting system, where people votes on defined risks based on their knowledge and sharing their opinion.
- Include shareholders distributions.
    - Another useful measure is the shareholder distribution.
- Define scenarios for financial companies, that require different metrics and only dividend scenarios.
    - The specified scenarios are not capable of valuating financial companies due to different metrics required.
- Inlcude MD&A section and financial notes analysis of 10-K and 10-Q, and other long sections.
    - Due to long text in MD&A and other sections we excluded their summaries. This problem need further text processing before using a LLM model to take it as input.